## Importing libraries

In [1]:
import pandas as pd
import numpy as np
import geopandas as gpd
import cenpy as cen
import altair as alt

/usr/local/lib/python3.9/site-packages/geopandas/_compat.py:111: UserWarning: The Shapely GEOS version (3.9.1-CAPI-1.14.2) is incompatible with the GEOS version PyGEOS was compiled with (3.10.1-CAPI-1.16.0). Conversions between both will be slow.
  warnings.warn(
/usr/local/lib/python3.9/site-packages/fuzzywuzzy/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [2]:
from apiKeys import *

## Downaloading Census Tracts (Geography)

In [3]:
nyStateCT2019 = gpd.read_file('https://www2.census.gov/geo/tiger/GENZ2019/shp/cb_2019_36_tract_500k.zip')
nycCT2019 = nyStateCT2019[nyStateCT2019['COUNTYFP'].isin(['005','047','061','081','085'])].copy(deep=True)


## Downloading 2019 ACS 5-year estimates data

In [4]:
# Setting a variable (con) for making a call to this specific table.
con = cen.remote.APIConnection('ACSDT5Y2019',apikey=censusKey)

# Setting the variables to download
columns = [
    'B01003_001', # Total Population
    'B02001_002', # White Population
    'B01001_008', # Male 20 years
    'B01001_009', # Male 21 years
    'B01001_010', # Male 22 - 24 years
    'B01001_011', # Male 25 - 29 years
    'B01001_012', # Male 30 - 34 years
    'B01001_032', # Female 20 years
    'B01001_033', # Female 21 years
    'B01001_034', # Female 22 - 24 years
    'B01001_035', # Female  25 - 29 years
    'B01001_036', # Female 30 - 34 years
    'B19013_001', # Median Household Income
    'B25064_001', # Median Gross Rent
    'B15001_017', # Male 24 - 34 Bachelor's degree
    'B15001_018', # Male 24 - 34 Graduate or professional degree
    'B15001_025', # Male 25 - 44 Bachelor's degree
    'B15001_026', # Male 25 - 44 Graduate or professional degree
    'B15001_033', # Male 45 - 64 Bachelor's degree
    'B15001_034', # Male 45 - 64 Graduate or professional degree
    'B15001_041', # Male 65 years and over Bachelor's degree
    'B15001_042', # Male 65 years and over Graduate or professional degree
    'B15001_058', # Female 24 - 34 Bachelor's degree
    'B15001_059', # Female 24 - 34 Graduate or professional degree
    'B15001_066', # Female 25 - 44 Bachelor's degree
    'B15001_067', # Female 25 - 44 Graduate or professional degree
    'B15001_074', # Female 45 - 64 Bachelor's degree
    'B15001_075', # Female 45 - 64 Graduate or professional degree
    'B15001_082', # Female 65 years and over Bachelor's degree
    'B15001_083', # Female 65 years and over Graduate or professional degree
]

# Creating the suffix for "estimates" and "margin of error"
columns_E = [i+'E' for i in columns]
# columns_M = [i+'M' for i in columns]

# Define the units of geography, as well as a filter for what we are looking for. 
g_unit = 'tract'
g_filter = {'state':'36'}

# Make an API call
# censusData2019 = con.query(columns_E + columns_M, geo_unit=g_unit, geo_filter=g_filter)
censusData2019 = con.query(columns_E, geo_unit=g_unit, geo_filter=g_filter)

In [5]:
censusData2019['NonWhite'] = (censusData2019['B02001_002E']).astype('int') / (censusData2019['B01003_001E']).astype('int')
censusData2019['Education'] = ((censusData2019['B15001_017E']).astype('int')+(censusData2019['B15001_018E']).astype('int')+(censusData2019['B15001_025E']).astype('int')+(censusData2019['B15001_026E']).astype('int')+(censusData2019['B15001_033E']).astype('int')+(censusData2019['B15001_034E']).astype('int')+(censusData2019['B15001_041E']).astype('int')+(censusData2019['B15001_042E']).astype('int')+(censusData2019['B15001_058E']).astype('int')+(censusData2019['B15001_059E']).astype('int')+(censusData2019['B15001_066E']).astype('int')+(censusData2019['B15001_067E']).astype('int')+(censusData2019['B15001_074E']).astype('int')+(censusData2019['B15001_075E']).astype('int')+(censusData2019['B15001_082E']).astype('int')+(censusData2019['B15001_083E']).astype('int')) / (censusData2019['B01003_001E']).astype('int')
censusData2019['Young'] = ((censusData2019['B01001_008E']).astype('int')+(censusData2019['B01001_009E']).astype('int')+(censusData2019['B01001_010E']).astype('int')+(censusData2019['B01001_011E']).astype('int')+(censusData2019['B01001_012E']).astype('int')+(censusData2019['B01001_032E']).astype('int')+(censusData2019['B01001_033E']).astype('int')+(censusData2019['B01001_034E']).astype('int')+(censusData2019['B01001_035E']).astype('int')+(censusData2019['B01001_036E']).astype('int'))/(censusData2019['B01003_001E']).astype('int')
censusData2019.rename(columns={'B01003_001E':'TotalPop','B19013_001E':'MedianHHI','B25064_001E':'MedianRent'},inplace=True)

In [6]:
censusData2019.drop(columns=['B02001_002E', 'B01001_008E', 'B01001_009E', 'B01001_010E',
       'B01001_011E', 'B01001_012E', 'B01001_032E', 'B01001_033E',
       'B01001_034E', 'B01001_035E', 'B01001_036E', 'B15001_017E',
       'B15001_018E', 'B15001_025E', 'B15001_026E', 'B15001_033E',
       'B15001_034E', 'B15001_041E', 'B15001_042E', 'B15001_058E',
       'B15001_059E', 'B15001_066E', 'B15001_067E', 'B15001_074E',
       'B15001_075E', 'B15001_082E', 'B15001_083E'], inplace=True)

In [7]:
censusData2019['GEOID'] = censusData2019['state']+censusData2019['county']+censusData2019['tract']

In [8]:
nycCensusData2019 = censusData2019[censusData2019['county'].isin(['005','047','061','081','085'])].copy(deep=True)

## Merging with 2000/2016 data

In [9]:
baseData = pd.read_excel('../input/previousCodeR/Data_NYC_Gentrification_2000_16.xlsx', dtype={'tractid':'str'})

In [10]:
baseData.drop(columns=['Unnamed: 9','Unnamed: 17','Unnamed: 23'], inplace=True)

In [11]:
nycCensusData2019.rename(columns={'TotalPop':'totpop19','NonWhite':'NHW19','Young':'A20_34y19','Education':'colleg19','MedianHHI':'mdfami19','MedianRent':'mdrent19'}, inplace=True)

In [12]:
nycCensusData2019[~nycCensusData2019['GEOID'].isin(baseData['tractid'])]

totpop19    mdfami19    mdrent19 state county   tract     NHW19  \
110         0  -666666666  -666666666    36    085  015400       NaN   
156       633  -666666666  -666666666    36    005  031900  0.620853   
223         0  -666666666  -666666666    36    081  079300       NaN   
417         0  -666666666  -666666666    36    081  064102       NaN   
472        49  -666666666  -666666666    36    081  005000  0.571429   
...       ...         ...         ...   ...    ...     ...       ...   
4655        0  -666666666  -666666666    36    081  010701       NaN   
4692       51  -666666666  -666666666    36    081  017100  0.529412   
4724       26  -666666666  -666666666    36    047  085200  0.000000   
4789        0  -666666666  -666666666    36    081  071600       NaN   
4844        0  -666666666  -666666666    36    081  024600       NaN   

      colleg19  A20_34y19        GEOID  
110        NaN        NaN  36085015400  
156   0.088468   0.552923  36005031900  
223        NaN        NaN  36081079300  
417        NaN        NaN  36081064102  
472   0.183673   0.183673  36081005000  
...        ...        ...          ...  
4655       NaN        NaN  36081010701  
4692  0.274510   0.176471  36081017100  
4724  0.615385   0.423077  36047085200  
4789       NaN        NaN  36081071600  
4844       NaN        NaN  36081024600  

[72 rows x 10 columns]

In [13]:
updatedData = baseData.merge(nycCensusData2019, left_on='tractid', right_on='GEOID', how='left')

In [14]:
updatedData.shape

(2095, 35)

## Performing statistical analysis

In [15]:
updatedData.isnull().values.any()

False

In [16]:
updatedData['mdfami19'] = updatedData['mdfami19'].astype('int')
updatedData['mdrent19'] = updatedData['mdrent19'].astype('int')
updatedData['totpop19'] = updatedData['totpop19'].astype('int')

In [17]:
updatedData['mdfami19'].replace(-666666666,0, inplace=True)
updatedData['mdrent19'].replace(-666666666,0, inplace=True)

In [18]:
updatedData.describe()

totpop00      pop24_00         NHW00    A20_34y00     colleg00  \
count   2095.000000   2095.000000   2095.000000  2095.000000  2095.000000   
mean    3785.318377   2492.870644   1348.973986   914.509785   685.470167   
std     2124.856050   1527.858643   1599.971114   624.142320   959.240836   
min      109.000000     94.000000      1.000000    15.000000     8.000000   
25%     2289.000000   1494.500000    132.500000   506.500000   214.000000   
50%     3372.000000   2142.000000    795.000000   764.000000   379.000000   
75%     4764.500000   3031.500000   2009.000000  1132.000000   750.000000   
max    24834.000000  18199.000000  13651.000000  4974.000000  9423.000000   

            mdfami00     mdrent00      totpop16      pop24_16         NHW16  \
count    2095.000000  2095.000000   2095.000000   2095.000000   2095.000000   
mean    49002.302148   754.276372   4029.698329   2786.037232   1301.718377   
std     28685.513790   232.965252   2176.970411   1596.583408   1544.104261   
min      9893.000000   195.000000    119.000000     91.000000      0.000000   
25%     30730.500000   644.000000   2493.000000   1700.500000    152.000000   
50%     42647.000000   741.000000   3639.000000   2464.000000    785.000000   
75%     59454.000000   835.000000   5092.000000   3447.500000   1882.000000   
max    200001.000000  2001.000000  29256.000000  21585.000000  12390.000000   

       ...    scores_raw  score_0.025    score_0.5  score_0.975      totpop19  \
count  ...  2.095000e+03  2095.000000  2095.000000  2095.000000   2095.000000   
mean   ... -2.386637e-12    -0.974691    -0.000131     0.974408   4010.026730   
std    ...  1.465995e+00     1.160516     1.155242     1.157117   2173.505449   
min    ... -7.114296e+00    -4.199366    -2.957045    -1.923782     98.000000   
25%    ... -9.395894e-01    -1.733470    -0.758742     0.200714   2461.500000   
50%    ... -3.142596e-01    -1.284226    -0.312749     0.672088   3603.000000   
75%    ...  6.441831e-01    -0.503421     0.472789     1.455440   5004.500000   
max    ...  7.767826e+00     3.571540     4.504303     5.654016  28109.000000   

            mdfami19     mdrent19        NHW19     colleg19    A20_34y19  
count    2095.000000  2095.000000  2095.000000  2095.000000  2095.000000  
mean    70930.031026  1547.504057     0.423964     0.262563     0.238830  
std     34874.590634   500.091320     0.290033     0.170702     0.079109  
min         0.000000     0.000000     0.000000     0.012656     0.003411  
25%     47547.500000  1313.500000     0.152324     0.140186     0.186910  
50%     66439.000000  1486.000000     0.394240     0.217689     0.224543  
75%     86548.500000  1719.000000     0.687424     0.335422     0.271997  
max    250001.000000  3501.000000     0.990415     0.841808     0.629450  

[8 rows x 29 columns]

In [19]:
updatedData.drop(columns=['totpop16', 'pop24_16', 'NHW16',
       'A20_34y16', 'College16', 'mdfami16', 'mdrent16', 'NHW00_16',
       'A20_34y00_16', 'College00_16', 'mdfami00_16', 'mdrent00_16',
       'scores_raw', 'score_0.025', 'score_0.5', 'score_0.975','GEOID'],inplace=True)

In [20]:
updatedData['NHW00_19'] = (updatedData['NHW19']/(updatedData['NHW00']/updatedData['totpop00']))-1
updatedData['A20_34y00_19'] = (updatedData['A20_34y19']/(updatedData['A20_34y00']/updatedData['pop24_00']))-1
updatedData['College00_19'] = (updatedData['colleg19']/(updatedData['colleg00']/updatedData['totpop00']))-1
updatedData['mdfami00_19'] = (updatedData['mdfami19']/updatedData['mdfami00'])-1
updatedData['mdrent00_19'] = (updatedData['mdrent19']/updatedData['mdrent00'])-1

In [21]:
updatedData['NHW00_19'].describe()

count    2095.000000
mean        4.837898
std        20.253715
min        -1.000000
25%        -0.081907
50%         0.179353
75%         2.629888
max       418.067892
Name: NHW00_19, dtype: float64

In [22]:
updatedData['A20_34y00_19'].describe()

count    2095.000000
mean       -0.333983
std         0.195618
min        -0.859283
25%        -0.454260
50%        -0.362546
75%        -0.245861
max         2.675477
Name: A20_34y00_19, dtype: float64

In [23]:
updatedData['College00_19'].describe()

count    2095.000000
mean        1.005293
std         1.436634
min        -0.623249
25%         0.220854
50%         0.588834
75%         1.222157
max        16.988227
Name: College00_19, dtype: float64

In [24]:
updatedData['mdfami00_19'].describe()

count    2095.000000
mean        0.554429
std         0.559263
min        -1.000000
25%         0.222181
50%         0.446891
75%         0.749664
max         7.629932
Name: mdfami00_19, dtype: float64

In [25]:
alt.Chart(updatedData).mark_point().encode(
    alt.X(alt.repeat("column"), type='quantitative'),
    alt.Y(alt.repeat("row"), type='quantitative')
).properties(
    width=200,
    height=200
).repeat(
    row=['mdfami00_19', 'A20_34y00_19', 'NHW00_19', 'College00_19', 'mdrent00_19'],
    column=['mdfami00_19', 'A20_34y00_19', 'NHW00_19', 'College00_19', 'mdrent00_19']
)

alt.RepeatChart(...)

In [26]:
alt.Chart(updatedData).mark_bar().encode(
    x=alt.X(alt.repeat('column'), type='quantitative', bin=alt.Bin(maxbins=20)),
    y=alt.Y('count()')
).repeat(
    column=['mdfami00_19', 'A20_34y00_19', 'NHW00_19', 'College00_19', 'mdrent00_19'],
)

alt.RepeatChart(...)

### Principal Component Analysis

Looking at [this tutorial](https://towardsdatascience.com/pca-using-python-scikit-learn-e653f8989e60)

* Should I transform the varaibles to `log` form before performing the PCA?

In [27]:
updatedData['mdfami00_19_log'] = np.log(updatedData['mdfami00_19']+1.01)
updatedData['A20_34y00_19_log'] = np.log(updatedData['A20_34y00_19']+1.01)
updatedData['NHW00_19_log'] = np.log(updatedData['NHW00_19']+1.01)
updatedData['College00_19_log'] = np.log(updatedData['College00_19']+1.01)
updatedData['mdrent00_19_log'] = np.log(updatedData['mdrent00_19']+1.01)

#### Standarize the data

In [28]:
from sklearn.preprocessing import StandardScaler

In [29]:
# Separating out the features
features = ['mdfami00_19', 'A20_34y00_19', 'NHW00_19', 'College00_19', 'mdrent00_19']
logFeatures = ['mdfami00_19_log', 'A20_34y00_19_log', 'NHW00_19_log', 'College00_19_log', 'mdrent00_19_log']

# Separating out the target
x = updatedData.loc[:, features].values
logX = updatedData.loc[:, logFeatures].values

# Standardizing the features
x = StandardScaler().fit_transform(x)
logX = StandardScaler().fit_transform(logX)

In [30]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)
principalComponents = pca.fit_transform(x)
logPrincipalComponents = pca.fit_transform(logX)
principalDf = pd.DataFrame(data = principalComponents, columns = ['pc1', 'pc2'])
principalDfLog = pd.DataFrame(data = logPrincipalComponents, columns = ['pc1_log', 'pc2_log'])

In [31]:
updatedData = pd.concat([updatedData, principalDf], axis = 1)
updatedData = pd.concat([updatedData, principalDfLog], axis = 1)

In [32]:
pca.explained_variance_ratio_

array([0.37498825, 0.21176135])

In [33]:
simplePCA = alt.Chart(updatedData).mark_point().encode(
    x=alt.X('pc1:Q'),
    y=alt.Y('pc2:Q'),
    tooltip='tractid',
    color=alt.Color('tractid:Q', scale=alt.Scale(scheme='magma'))
).properties(
    title='PCA with non-log inputs',
)
logPCA = alt.Chart(updatedData).mark_point().encode(
    x=alt.X('pc1_log:Q'),
    y=alt.Y('pc2_log:Q'),
    tooltip='tractid',
    color=alt.Color('tractid:Q', scale=alt.Scale(scheme='magma'))
).properties(
    title='PCA with log inputs',
)
simplePCA | logPCA

alt.HConcatChart(...)

In [34]:
updatedData.to_csv('../output/Data_NYC_Gentrification_2000_2019.csv', index=False)

### Spatial smoothing

Following [this](https://splot.readthedocs.io/en/stable/users/tutorials/smoothing.html)

1. Import libraries
2. Build spatial weights object
3. Build the smoothing object
4. Calculate the rate

#### Importing libraries

In [ ]:
from libpysal import weights
from esda import smoothing as sm

#### Building the spatial weights object

In [ ]:
nycData = nycCT2019.merge(finalDf, left_on='GEOID', right_on='tractid', how='inner')

In [ ]:
finalDf[~finalDf['tractid'].isin(nycData['GEOID'])]

In [ ]:
w = weights.Rook.from_dataframe(nycData)

#### Trying spatial lag

In [ ]:
nycData['pc1lag'] = weights.spatial_lag.lag_spatial(w, nycData['pc1'])
nycData['pc2lag'] = weights.spatial_lag.lag_spatial(w, nycData['pc2'])

In [ ]:
nycData['pc1'].describe()

In [ ]:
nycData['pc1lag'].describe()

In [ ]:
pc1Map = alt.Chart(nycData).mark_geoshape().encode(
    color=alt.Color('pc1:Q',
    legend=alt.Legend(title='PCA Variable 1'))
).properties(
    width=500,
    height=500
)
pc1lagMap = alt.Chart(nycData).mark_geoshape().encode(
    color=alt.Color('pc1lag:Q',
    legend=alt.Legend(title='PCA Lag Variable 1'))
).properties(
    width=500,
    height=500
)
pc2Map = alt.Chart(nycData).mark_geoshape().encode(
    color=alt.Color('pc2:Q',
    legend=alt.Legend(title='PCA Variable 2'))
).properties(
    width=500,
    height=500
)
pc2lagMap = alt.Chart(nycData).mark_geoshape().encode(
    color=alt.Color('pc2lag:Q',
    legend=alt.Legend(title='PCA Lag Variable 2'))
).properties(
    width=500,
    height=500
)
alt.vconcat(alt.hconcat(pc1Map,pc1lagMap).resolve_scale(color='independent'), alt.hconcat(pc2Map,pc2lagMap).resolve_scale(color='independent')).configure_view(
    stroke=None
)

#### Trying Kernel Smoothing

Following [this documentation](https://github.com/pysal/esda/blob/master/esda/smoothing.py#L979)

In [ ]:
from libpysal.weights.distance import Kernel

In [ ]:
nycData.to_crs('epsg:2263', inplace=True)

In [ ]:
centroids = list(zip(nycData['geometry'].centroid.x,nycData['geometry'].centroid.y))

In [ ]:
# Creating a kernel-based spatial weights instance by using the above points
kw=Kernel(centroids)

In [ ]:
if not kw.id_order_set: kw.id_order = range(0,len(centroids))

In [ ]:
kr1 = sm.Kernel_Smoother(nycData['pc1'], nycData['totpop19'], kw)
kr2 = sm.Kernel_Smoother(nycData['pc2'], nycData['totpop19'], kw)

In [ ]:
nycData['kr1'] = kr1.r
nycData['kr2'] = kr2.r

In [ ]:
nycData.to_crs('epsg:4326', inplace=True)

In [ ]:
pc1Map = alt.Chart(nycData).mark_geoshape().encode(
    color=alt.Color('pc1:Q',
    legend=alt.Legend(title='PCA variable 1'))
).properties(
    height=500,
    width=500
)
kr1Map = alt.Chart(nycData).mark_geoshape().encode(
    color=alt.Color('kr1:Q',
    legend=alt.Legend(title='Kernel smoothing variable 1'))
)
pc2Map = alt.Chart(nycData).mark_geoshape().encode(
    color=alt.Color('pc2:Q',
    legend=alt.Legend(title='PCA variable 2'))
).properties(
    height=500,
    width=500
)
kr2Map = alt.Chart(nycData).mark_geoshape().encode(
    color=alt.Color('kr2:Q',
    legend=alt.Legend(title='Kernel smoothing variable 2'))
)
alt.vconcat(alt.hconcat(pc1Map,kr1Map).resolve_scale(color='independent'),alt.hconcat(pc2Map,kr2Map).resolve_scale(color='independent')).configure_view(stroke=None)

#### Trying the empirical bayesian smoothing (not working)

In [ ]:
w.id_order

In [ ]:
if not w.id_order_set: w.id_order = range(1,len(nycData) + 1)

In [ ]:
for i,wi in enumerate(w):
    print(i, wi[0])

In [ ]:
len(w.id_order)

In [ ]:
w.id_order=range(1,2095)

In [ ]:
w[0]

In [ ]:
from esda.smoothing import Spatial_Empirical_Bayes

In [ ]:
nycData.columns

In [ ]:
s_eb = Spatial_Empirical_Bayes(nycData['pc1'], nycData['totpop19'], w)

In [ ]:
>>> import libpysal
    >>> stl_ex = libpysal.examples.load_example('stl')
    >>> stl = libpysal.io.open(stl_ex.get_path('stl_hom.csv'), 'r')
    The 11th and 14th columns in stl_hom.csv includes the number of homocides and population.
    Creating two arrays from these columns.
    >>> stl_e, stl_b = np.array(stl[:,10]), np.array(stl[:,13])
    Creating a spatial weights instance by reading in stl.gal file.
    >>> stl_w = libpysal.io.open(stl_ex.get_path('stl.gal'), 'r').read()
    Ensuring that the elements in the spatial weights instance are ordered
    by the given sequential numbers from 1 to the number of observations in stl_hom.csv
    >>> if not stl_w.id_order_set: stl_w.id_order = range(1,len(stl) + 1)
    Creating an instance of Spatial_Empirical_Bayes class using stl_e, stl_b, and stl_w
    >>> from esda.smoothing import Spatial_Empirical_Bayes
    >>> s_eb = Spatial_Empirical_Bayes(stl_e, stl_b, stl_w)
    Extracting the risk values through the property r of s_eb
    >>> s_eb.r[:10]
    array([[4.01485749e-05],
           [3.62437513e-05],
           [4.93034844e-05],
           [5.09387329e-05],
           [3.72735210e-05],
           [3.69333797e-05],
           [5.40245456e-05],
           [2.99806055e-05],
           [3.73034109e-05],
           [3.47270722e-05]])

In [ ]:
e, b = sm.sum_by_n(e, np.ones(12), 6), sm.sum_by_n(b, np.ones(12), 6)
rate = sm.Spatial_Empirical_Bayes(e, b, kw)
rate.r

TODO:

* Look at [this](https://popfactfinder.planning.nyc.gov/about) on how to compare different years
* Do hierarchical cluster analysis with geography (pysal) to see if they overlap with remediation locations
* Plot one pc1 against pc2 and see if there are clusters. This might show that there are a couple of value having a lot of effect.
* Do histograms before calculating the pca, and if the data looks like a hockey stick, do the log, or the square root before that.